In [2]:
--- Libraries:
arguments = require 'Settings.arguments'
constants = require 'Settings.constants'
card_to_string = require 'Game.card_to_string_conversion'
card_tools = require 'Game.card_tools'
game_settings = require 'Settings.game_settings'
Plot = require 'itorch.Plot'
nninit = require 'nninit'
require 'torch'
require 'math'
require 'Tree.tree_builder'
require 'Tree.tree_data_generation'
require 'Tree.tree_values'
require 'Tree.tree_visualiser'
require 'nn'
require 'Tree.tree_cfr'
require 'Tree.tree_cfr2'
require 'nngraph'
require 'optim'
require 'image'
require 'NN.strategy_net_builder'
require 'NN.strategy_net_trainer'
require 'Tree.tree_warm_start'
require 'Nn.StrategyCriterion'




In [3]:
--- Create the tree
builder = PokerTreeBuilder()
--- Parameters for the tree
params = {}
params.root_node = {}
params.root_node.board = card_to_string:string_to_board('As')
params.root_node.street = 2
params.root_node.current_player = constants.players.P1
params.root_node.bets = arguments.Tensor{200, 200}
--- CFR Solver
starting_ranges = arguments.Tensor(constants.players_count, game_settings.card_count)
starting_ranges[1]:copy(card_tools:get_uniform_range(params.root_node.board))
starting_ranges[2]:copy(card_tools:get_uniform_range(params.root_node.board))

In [4]:
--- Get Data from 2000 iterations
number_of_iterations = 1000
train_tree = builder:build_tree(params)
data = TreeData(train_tree)
train_tree_cfr = TreeCFR()
train_tree_cfr:run_cfr(train_tree, starting_ranges,number_of_iterations)
data:get_training_set(train_tree,1)

### Training the Model

In [5]:
-- Building the neural net model
nn_builder = StrategyNN()
nn_model = nn_builder.model
-- Building trainer:
nn_trainer = NNTrainer(data,nn_model)
-- Options:
opt = {}
opt.learningRate = 0.001
opt.momentum = 0.85
---opt.adam = true
---opt.nesterov = true
opt.validate = true

In [6]:
current_criterion = nn.SmoothL1Criterion()
train_lossL1,test_lossL1 = nn_trainer:train(nn_model,current_criterion,opt,10000)
err_smooth = torch.FloatTensor(nn_trainer.table_abs_error):clone()

In [7]:
local num_iter = torch.range(1,train_lossL1:size(1))
local plot = Plot()

plot:line(num_iter,train_lossL1,'black' ,'No Warm start CFR = Uniform warm start')
plot:line(num_iter,test_lossL1,'red' ,'No Warm start CFR = Uniform warm start')
plot:xaxis('Number of iterations'):yaxis('Loss'):redraw()

In [8]:
pred_strat = nn_model:forward({nn_trainer.all_data.features,nn_trainer.all_data.masks})
true_strat =nn_trainer.all_data.targets
print(torch.mean(torch.abs(pred_strat- true_strat)))

0.15639660002974


In [ ]:
local num_iter = torch.range(1,err_smooth:size(1))
local plot = Plot()

plot:line(num_iter,err_smooth,'red','Smooth Huber Loss')
plot:line(num_iter,err_cross,'blue','Cross Entropy Loss')
plot:legend(true):title('Mean Absolute Error Huber vs Cross Entropy')
plot:xaxis('Number of iterations'):yaxis('Mean Absolute Error')
plot:draw()

In [9]:
-- Building the neural net model
nn_builder = StrategyNN()
nn_model = nn_builder.model
-- Building trainer:
nn_trainer = NNTrainer(data,nn_model)
-- Options:
opt = {}
opt.learningRate = 0.001
opt.momentum = 0.85
opt.validate = true
opt.weightDecay = 0.65
opt.nesterov = true
---opt.adam = true

In [10]:
strategy_criterion = StrategyLoss()
train_loss,test_loss = nn_trainer:train(nn_model,strategy_criterion,opt,10000)
err_cross = torch.FloatTensor(nn_trainer.table_abs_error):clone()

In [11]:
pred_strat = nn_model:forward({nn_trainer.all_data.features,nn_trainer.all_data.masks})
true_strat = nn_trainer.all_data.targets
print(torch.mean(torch.abs(pred_strat- true_strat)))

0.0074845033580927


In [12]:
local num_iter = torch.range(1,train_loss:size(1))
local plot = Plot()

plot:line(num_iter,train_loss,'black' ,'No Warm start CFR = Uniform warm start')
plot:line(num_iter,test_loss,'red' ,'No Warm start CFR = Uniform warm start')
plot:xaxis('Number of iterations'):yaxis('Loss'):redraw()

In [14]:
train_matrix_L1 = torch.FloatTensor()
test_matrix_L1 = torch.FloatTensor()
number_iter = 5000
error_smooth = torch.FloatTensor()

for i = 1,50 do
    -- Building the neural net model
    nn_builder = StrategyNN()
    nn_model = nn_builder.model
    -- Building trainer:
    nn_trainer = NNTrainer(data,nn_model)
    -- Options:
    opt = {}
    opt.learningRate = 0.001
    opt.momentum = 0.85
    opt.validate = true
    opt.weightDecay = 0.75
    ---opt.nesterov = true
    ---strategy_criterion = StrategyLoss()
    strategy_criterion = nn.SmoothL1Criterion()
    train_loss,test_loss = nn_trainer:train(nn_model,strategy_criterion,opt,number_iter)
    train_matrix_L1 = train_matrix_L1:cat(train_loss:view(1,number_iter):clone(),1)
    test_matrix_L1 = test_matrix_L1:cat(test_loss:view(1,number_iter):clone(),1)
    error_smooth = error_smooth:cat(torch.FloatTensor(nn_trainer.table_abs_error):clone(),2)
end

In [15]:
local num_iter = torch.range(1,train_loss:size(1))
local plot = Plot()

plot:line(num_iter,train_matrix_L1:mean(1):view(-1),'blue','Average Train Error')
plot:line(num_iter,1.96*train_matrix_L1:std(1):view(-1)+train_matrix_L1:mean(1):view(-1),'gray','Upper Bound 95% - Train error' )
plot:line(num_iter,-1.96*train_matrix_L1:std(1):view(-1)+train_matrix_L1:mean(1):view(-1),'gray','Lower Bound 95% - Train error')
plot:line(num_iter,1.96*test_matrix_L1:std(1):view(-1)+test_matrix_L1:mean(1):view(-1),'violet','Upper Bound 95% - Test error' )
plot:line(num_iter,-1.96*test_matrix_L1:std(1):view(-1)+test_matrix_L1:mean(1):view(-1),'violet','Lower Bound 95% - Test error' )
plot:line(num_iter,test_matrix_L1:mean(1):view(-1),'red','Average Test Error')
plot:legend(true):title('Train error vs Test error - Huber Loss ')
plot:xaxis('Number of iterations'):yaxis('Loss')
plot:draw()

In [16]:
train_matrix = torch.FloatTensor()
test_matrix = torch.FloatTensor()
number_iter = 5000
error_cross = torch.FloatTensor()

for i = 1,10 do
    -- Building the neural net model
    nn_builder = StrategyNN()
    nn_model = nn_builder.model
    -- Building trainer:
    nn_trainer = NNTrainer(data,nn_model)
    -- Options:
    opt = {}
    opt.learningRate = 0.001
    opt.momentum = 0.85
    opt.validate = true
    opt.weightDecay = 0.75
    ---opt.nesterov = true
    strategy_criterion = StrategyLoss()
    ---strategy_criterion = nn.SmoothL1Criterion()
    train_loss,test_loss = nn_trainer:train(nn_model,strategy_criterion,opt,number_iter)
    train_matrix = train_matrix:cat(train_loss:view(1,number_iter):clone(),1)
    test_matrix = test_matrix:cat(test_loss:view(1,number_iter):clone(),1)
    error_cross = error_cross:cat(torch.FloatTensor(nn_trainer.table_abs_error):clone(),2)
end
print(error_cross:mean())

0.076919371888712


In [17]:
local num_iter = torch.range(1,train_loss:size(1))
local plot = Plot()

plot:line(num_iter,train_matrix:mean(1):view(-1),'blue','Average Train Error')
plot:line(num_iter,1.96*train_matrix:std(1):view(-1)+train_matrix:mean(1):view(-1),'gray','Upper Bound 95% - Train error' )
plot:line(num_iter,-1.96*train_matrix:std(1):view(-1)+train_matrix:mean(1):view(-1),'gray','Lower Bound 95% - Train error')
plot:line(num_iter,1.96*test_matrix:std(1):view(-1)+test_matrix:mean(1):view(-1),'violet','Upper Bound 95% - Test error' )
plot:line(num_iter,-1.96*test_matrix:std(1):view(-1)+test_matrix:mean(1):view(-1),'violet','Lower Bound 95% - Test error' )
plot:line(num_iter,test_matrix:mean(1):view(-1),'red','Average Test Error')
plot:legend(true):title('Train error vs Test error - Cross Entropy Loss ')
plot:xaxis('Number of iterations'):yaxis('Loss')
plot:draw()

In [ ]:
local num_iter = torch.range(1,error_smooth:mean(2):size(1))
local plot = Plot()

plot:line(num_iter,error_smooth:mean(2),'red','Smooth Huber Loss')
plot:line(num_iter,error_cross:mean(2),'blue','Cross Entropy Loss')
plot:legend(true):title('Mean Absolute Error Huber vs Cross Entropy')
plot:xaxis('Number of iterations'):yaxis('Mean Absolute Error')
plot:draw()